In [55]:
from pulp import LpMaximize, LpProblem, LpStatus, lpSum, LpVariable
import pandas as pd
import numpy as np

import sys
sys.setrecursionlimit(1000000)

In [387]:
# Create the model
model = LpProblem(name="model", sense=LpMaximize)

number_of_students = 31
number_of_fulltimes = 8
days_of_week = 5
daily_time_slots = 28
shift_length = 7
weekly_time_slots = days_of_week * daily_time_slots
daily_shifts = daily_time_slots
weekly_shifts = days_of_week * daily_shifts

# Initialize the decision variables
for i in range(1, number_of_students + 1):
    for j in range(1, weekly_shifts + 1):
        for k in ["Z", "P", "H"]:
            str = 'x_{0}_{1}_{2} = LpVariable("x_{3}_{4}_{5}", lowBound=0, upBound = 1, cat=\'Integer\')'.format(i,j,k,i,j,k)
            exec(str)

In [388]:
# Define sets

# Create sets for hours of operations and peak hours of the week
Z = list()
Z_peak = list()
H = list()
H_peak = list()
P = list()
P_peak = list()

Z_start = 3 + 6
Z_end = 23 + 6
Z_peak_start = 5 + 6
Z_peak_end = 21 + 6
H_start = 3 + 6
H_end = 21 + 6
H_peak_start = 9 + 6
H_peak_end = 13 + 6
P_start = 1 + 6
P_end = 21 + 6
P_peak_start = 7 + 6
P_peak_end =15 + 6

for day in range(days_of_week):
    Z.extend(list(range(Z_start + daily_time_slots * day, Z_end + daily_time_slots * day)))
    Z_peak.extend(list(range(Z_peak_start + daily_time_slots * day, Z_peak_end + daily_time_slots * day)))
    H.extend(list(range(H_start + daily_time_slots * day, H_end + daily_time_slots * day)))
    H_peak.extend(list(range(H_peak_start + daily_time_slots * day, H_peak_end + daily_time_slots * day)))
    P.extend(list(range(P_start + daily_time_slots * day, P_end + daily_time_slots * day)))
    P_peak.extend(list(range(P_peak_start + daily_time_slots * day, P_peak_end+daily_time_slots * day)))

    
# Read in Student and Full time availability matrices
As = pd.read_excel("./Student_availability_matrix.xlsx")
Af = pd.read_excel("./Fulltime_availability_df.xlsx")


In [389]:
# Add the constraints to the model

# C1
for i in range(1, number_of_students + 1): # loop through all student baristas
    for j in range(1, weekly_shifts + 1): # loop through all the possible shifts
        for k in ["Z", "H", "P"]:
            if As.loc[j-1][i] == 0:
                C_1 = 'x_{0}_{1}_{2}'.format(i,j,k)
                model += (eval(C_1) <= 0, 'C1 constraint for student {0} at time slot {1} location {2}'.format(i,j,k))

In [390]:
# C2
for t in Z: # at each operation time slot t
    
    # initialize the constraint funciton
    C_2 = ""
    
    # add all students who are working at that time slot t
    for i in range(7, number_of_students + 1): 
        # NOTE: this will add everyone who started working up to 6 time slots before that time slot
        for l in range(0, shift_length):
            C_2 += 'x_{0}_{1}_Z + '.format(i,t - l)
    
     # add all full-times who are working at that time slot
    for m in range(1, number_of_fulltimes + 1):
        f_z = Af["Suzzallo"][t-1] # number of full-time working at Suzzallo at time slot t

    C_2 = C_2[:-2] # remove the last plus sign
    
    # Add constraints for time slot t into the model
    model += (eval(C_2) <= 10 - f_z,
              'C2 upperbound constraint for time slot {0} at Suzzallo'.format(t))
    model += (eval(C_2) >= 5 - f_z,
              'C2 lowerbound constraint for time slot {0} at Suzzallo'.format(t))

In [391]:
# C3
for t in H: # at each operation time slot t
    
    # initialize the constraint funciton
    C_3 = ""
    
    # add all students who are working at time slot t
    for i in range(7, number_of_students + 1): 
        # NOTE: this will add everyone who started working up to 6 time slots before time slot t
        for l in range(0, shift_length):
            C_3 += 'x_{0}_{1}_H + '.format(i,t - l)
    
     # add all full-times who are working at that time slot
    for m in range(1, number_of_fulltimes + 1):
        f_h = Af["HUB"][t-1] # number of full-time working at Suzzallo at time slot t
        
    C_3 = C_3[:-2] # remove the last plus sign
    
    # Add constraints for time slot t into the model
    model += (eval(C_3) <= 6 - f_h,
              'C3 upperbound constraint for time slot {0} at HUB'.format(t))
    model += (eval(C_3) >= 4 - f_h,
              'C3 lowerbound constraint for time slot {0} at HUB'.format(t))

In [392]:
# C4
for t in P: # at each operation time slot t
    
    # initialize the constraint funciton
    C_4 = ""
    
    # add all students who are working at time slot t
    for i in range(1, number_of_students + 1): 
        # NOTE: this will add everyone who started working up to 6 time slots before time slot t
        for l in range(0, shift_length):
            C_4 += 'x_{0}_{1}_P + '.format(i,t - l)
    
     # add all full-times who are working at that time slot
    for m in range(1, number_of_fulltimes + 1):
        f_p = Af["Pop.Health"][t-1] # number of full-time working at Suzzallo time slot t

    C_4 = C_4[:-2] # remove the last plus sign
    
    # Add constraints for time slot t into the model
    model += (eval(C_4) <= 7 - f_p,
              'C4 upperbound constraint for time slot {0} at Pop Health'.format(t))
    model += (eval(C_4) >= 4 - f_p,
              'C4 lowerbound constraint for time slot {0} at Pop Health'.format(t))

In [372]:
# C5

# Loop through each student
for i in range(1, number_of_students + 1):
    # Loop through all time slots
    for time in range(7, weekly_time_slots + 1):
        C_5 = ""
        # If it is not within the operation hours
        if time not in Z:
            for l in range(0, shift_length):
                # there should not be shift scheduled at this location
                    C_5 += 'x_{0}_{1}_Z +'.format(i, time - l)
            C_5 = C_5[:-2] # remove the last plus sign
            model += (eval(C_5) <= 0, 'C5 constraint for student {0} for time slot {1}'.format(i, time))
        else:
            pass

In [349]:
# C6

# Loop through each student
for i in range(1, number_of_students + 1):
    # Loop through all time slots
    for time in range(7, weekly_time_slots + 1):
        C_6 = ""
        # If it is not within the operation hours
        if time not in H:
            for l in range(0, shift_length):
                # there should not be shift scheduled at this location
                C_6 += 'x_{0}_{1}_H +'.format(i, time - l)
            C_6 = C_6[:-2] # remove the last plus sign
            model += (eval(C_6) <= 0, 'C6 constraint for student {0} for time slot {1}'.format(i, time))
        else:
            pass

In [350]:
# C7

# Loop through each student
for i in range(1, number_of_students + 1):
    # Loop through all time slots
    for time in range(7, weekly_time_slots + 1):
        C_7 = ""
        # If it is not within the operation hours
        if time not in P:
            for l in range(0, shift_length):
                # there should not be shift scheduled at this location
                C_7 += 'x_{0}_{1}_P +'.format(i, time - l)
            C_7 = C_7[:-2] # remove the last plus sign
            model += (eval(C_7) <= 0, 'C7 constraint for student {0} for time slot {1}'.format(i, time))
        else:
            pass

In [393]:
# C8

# Loop through each student
for i in range(1, number_of_students + 1):
    # For every day
    for day in range(days_of_week):
        C_8 = ""
        
        # Add all the shifts they have that day
        for t in range(1, daily_shifts + 1):
            # in each location
            for k in ["Z", "H", "P"]:
                C_8 += 'x_{0}_{1}_{2} +'.format(i, day * daily_shifts + t, k)
                
        C_8 = C_8[:-2] # remove the last plus sign        
        model += (eval(C_8) <= 1, 'C8 constraint at day {0} for student {1}'.format(day + 1,i))

In [394]:
# Define objective function (F1)
F_1 = ""
for i in range(1, number_of_students + 1):
    for j in Z_peak:
        for l in range(0, shift_length):
            F_1 += 'x_{0}_{1}_Z + '.format(i,j-l)
    for j in H_peak:
        for l in range(0, shift_length):
            F_1 += 'x_{0}_{1}_H + '.format(i,j-l)
    for j in P_peak:
        for l in range(0, shift_length):
            F_1 += 'x_{0}_{1}_P + '.format(i,j-l)

F_1 = F_1[:-2] # remove the last plus sign

model += eval(F_1)

In [395]:
model

model:
MAXIMIZE
3*x_10_100_H + 5*x_10_100_P + 7*x_10_100_Z + 2*x_10_101_H + 4*x_10_101_P + 7*x_10_101_Z + 1*x_10_102_H + 3*x_10_102_P + 7*x_10_102_Z + 2*x_10_103_P + 7*x_10_103_Z + 1*x_10_104_P + 7*x_10_104_Z + 6*x_10_105_Z + 5*x_10_106_Z + 4*x_10_107_Z + 3*x_10_108_Z + 2*x_10_109_Z + 2*x_10_10_H + 4*x_10_10_P + 6*x_10_10_Z + 1*x_10_110_Z + 1*x_10_117_Z + 2*x_10_118_Z + 1*x_10_119_P + 3*x_10_119_Z + 3*x_10_11_H + 5*x_10_11_P + 7*x_10_11_Z + 2*x_10_120_P + 4*x_10_120_Z + 1*x_10_121_H + 3*x_10_121_P + 5*x_10_121_Z + 2*x_10_122_H + 4*x_10_122_P + 6*x_10_122_Z + 3*x_10_123_H + 5*x_10_123_P + 7*x_10_123_Z + 4*x_10_124_H + 6*x_10_124_P + 7*x_10_124_Z + 4*x_10_125_H + 7*x_10_125_P + 7*x_10_125_Z + 4*x_10_126_H + 7*x_10_126_P + 7*x_10_126_Z + 4*x_10_127_H + 6*x_10_127_P + 7*x_10_127_Z + 3*x_10_128_H + 5*x_10_128_P + 7*x_10_128_Z + 2*x_10_129_H + 4*x_10_129_P + 7*x_10_129_Z + 4*x_10_12_H + 6*x_10_12_P + 7*x_10_12_Z + 1*x_10_130_H + 3*x_10_130_P + 7*x_10_130_Z + 2*x_10_131_P + 7*x_10_131_Z + 1*x

In [396]:
status = model.solve()

print(f"status: {model.status}, {LpStatus[model.status]}")
print(f"objective: {model.objective.value()}")

for var in model.variables():
    print(f"{var.name}: {var.value()}")

for name, constraint in model.constraints.items():
    print(f"{name}: {constraint.value()}")

status: -1, Infeasible
objective: -4844.0
x_10_100_H: 0.0
x_10_100_P: 0.0
x_10_100_Z: 0.0
x_10_101_H: 0.0
x_10_101_P: 0.0
x_10_101_Z: 0.0
x_10_102_H: 0.0
x_10_102_P: 0.0
x_10_102_Z: 0.0
x_10_103_H: 0.0
x_10_103_P: 0.0
x_10_103_Z: 0.0
x_10_104_H: 0.0
x_10_104_P: -19.0
x_10_104_Z: 0.0
x_10_105_H: 0.0
x_10_105_P: 0.0
x_10_105_Z: 0.0
x_10_106_H: 0.0
x_10_106_P: 0.0
x_10_106_Z: 0.0
x_10_107_H: 0.0
x_10_107_P: 0.0
x_10_107_Z: 0.0
x_10_108_H: 0.0
x_10_108_P: 0.0
x_10_108_Z: 0.0
x_10_109_H: 0.0
x_10_109_P: 0.0
x_10_109_Z: 0.0
x_10_10_H: 0.0
x_10_10_P: 0.0
x_10_10_Z: 0.0
x_10_110_H: 0.0
x_10_110_P: 0.0
x_10_110_Z: 0.0
x_10_111_H: 0.0
x_10_111_P: 0.0
x_10_111_Z: 0.0
x_10_112_H: 0.0
x_10_112_P: 0.0
x_10_112_Z: 0.0
x_10_113_H: 0.0
x_10_113_P: 0.0
x_10_113_Z: 0.0
x_10_114_H: 0.0
x_10_114_P: 0.0
x_10_114_Z: 0.0
x_10_115_H: 0.0
x_10_115_P: 0.0
x_10_115_Z: 0.0
x_10_116_H: 0.0
x_10_116_P: 0.0
x_10_116_Z: 0.0
x_10_117_H: 0.0
x_10_117_P: 0.0
x_10_117_Z: 0.0
x_10_118_H: 0.0
x_10_118_P: 0.0
x_10_118_Z: 0.0

x_13_108_P: 0.0
x_13_108_Z: 0.0
x_13_109_H: 0.0
x_13_109_P: 0.0
x_13_109_Z: 0.0
x_13_10_H: 0.0
x_13_10_P: 0.0
x_13_10_Z: 0.0
x_13_110_H: 0.0
x_13_110_P: 0.0
x_13_110_Z: 0.0
x_13_111_H: 0.0
x_13_111_P: 0.0
x_13_111_Z: 0.0
x_13_112_H: 0.0
x_13_112_P: 0.0
x_13_112_Z: 0.0
x_13_113_H: 0.0
x_13_113_P: 0.0
x_13_113_Z: 0.0
x_13_114_H: 0.0
x_13_114_P: 0.0
x_13_114_Z: 0.0
x_13_115_H: 0.0
x_13_115_P: 0.0
x_13_115_Z: 0.0
x_13_116_H: 0.0
x_13_116_P: 0.0
x_13_116_Z: 0.0
x_13_117_H: 0.0
x_13_117_P: 0.0
x_13_117_Z: 0.0
x_13_118_H: 0.0
x_13_118_P: 0.0
x_13_118_Z: 0.0
x_13_119_H: 0.0
x_13_119_P: 0.0
x_13_119_Z: 0.0
x_13_11_H: 0.0
x_13_11_P: 0.0
x_13_11_Z: 0.0
x_13_120_H: 0.0
x_13_120_P: 0.0
x_13_120_Z: 0.0
x_13_121_H: 0.0
x_13_121_P: 0.0
x_13_121_Z: 0.0
x_13_122_H: 0.0
x_13_122_P: 0.0
x_13_122_Z: 0.0
x_13_123_H: 0.0
x_13_123_P: 0.0
x_13_123_Z: 0.0
x_13_124_H: 0.0
x_13_124_P: 0.0
x_13_124_Z: 0.0
x_13_125_H: 0.0
x_13_125_P: 1.0
x_13_125_Z: 0.0
x_13_126_H: 0.0
x_13_126_P: 0.0
x_13_126_Z: 0.0
x_13_127_H: 0.

x_15_29_P: 0.0
x_15_29_Z: 0.0
x_15_2_H: 0.0
x_15_2_P: 0.0
x_15_2_Z: 0.0
x_15_30_H: 0.0
x_15_30_P: 0.0
x_15_30_Z: 0.0
x_15_31_H: 0.0
x_15_31_P: 0.0
x_15_31_Z: 0.0
x_15_32_H: 0.0
x_15_32_P: 0.0
x_15_32_Z: 0.0
x_15_33_H: 0.0
x_15_33_P: 0.0
x_15_33_Z: 0.0
x_15_34_H: 0.0
x_15_34_P: 0.0
x_15_34_Z: 0.0
x_15_35_H: 0.0
x_15_35_P: 0.0
x_15_35_Z: 0.0
x_15_36_H: 0.0
x_15_36_P: 0.0
x_15_36_Z: 0.0
x_15_37_H: 0.0
x_15_37_P: 0.0
x_15_37_Z: 0.0
x_15_38_H: 0.0
x_15_38_P: 0.0
x_15_38_Z: 0.0
x_15_39_H: 0.0
x_15_39_P: 0.0
x_15_39_Z: 0.0
x_15_3_H: 0.0
x_15_3_P: 0.0
x_15_3_Z: 0.0
x_15_40_H: 0.0
x_15_40_P: 0.0
x_15_40_Z: 0.0
x_15_41_H: 0.0
x_15_41_P: 0.0
x_15_41_Z: 0.0
x_15_42_H: 0.0
x_15_42_P: 0.0
x_15_42_Z: 0.0
x_15_43_H: 0.0
x_15_43_P: 0.0
x_15_43_Z: 0.0
x_15_44_H: 0.0
x_15_44_P: 0.0
x_15_44_Z: 0.0
x_15_45_H: 0.0
x_15_45_P: 0.0
x_15_45_Z: 0.0
x_15_46_H: 0.0
x_15_46_P: 0.0
x_15_46_Z: 0.0
x_15_47_H: 0.0
x_15_47_P: 0.0
x_15_47_Z: 0.0
x_15_48_H: 0.0
x_15_48_P: 0.0
x_15_48_Z: 0.0
x_15_49_H: 0.0
x_15_49_P: 0.0
x

x_19_101_P: 0.0
x_19_101_Z: 0.0
x_19_102_H: 0.0
x_19_102_P: 0.0
x_19_102_Z: 0.0
x_19_103_H: 0.0
x_19_103_P: 0.0
x_19_103_Z: 0.0
x_19_104_H: 0.0
x_19_104_P: 0.0
x_19_104_Z: 0.0
x_19_105_H: 0.0
x_19_105_P: 0.0
x_19_105_Z: 0.0
x_19_106_H: 0.0
x_19_106_P: 0.0
x_19_106_Z: 0.0
x_19_107_H: 0.0
x_19_107_P: 0.0
x_19_107_Z: 0.0
x_19_108_H: 0.0
x_19_108_P: 0.0
x_19_108_Z: 0.0
x_19_109_H: 0.0
x_19_109_P: 0.0
x_19_109_Z: 0.0
x_19_10_H: 0.0
x_19_10_P: 0.0
x_19_10_Z: 0.0
x_19_110_H: 0.0
x_19_110_P: 0.0
x_19_110_Z: 0.0
x_19_111_H: 0.0
x_19_111_P: 0.0
x_19_111_Z: 0.0
x_19_112_H: 0.0
x_19_112_P: 0.0
x_19_112_Z: 0.0
x_19_113_H: 0.0
x_19_113_P: 0.0
x_19_113_Z: 0.0
x_19_114_H: 0.0
x_19_114_P: 0.0
x_19_114_Z: 0.0
x_19_115_H: 0.0
x_19_115_P: 0.0
x_19_115_Z: 0.0
x_19_116_H: 0.0
x_19_116_P: 0.0
x_19_116_Z: 0.0
x_19_117_H: 0.0
x_19_117_P: 0.0
x_19_117_Z: 0.0
x_19_118_H: 0.0
x_19_118_P: 0.0
x_19_118_Z: 0.0
x_19_119_H: 0.0
x_19_119_P: 0.0
x_19_119_Z: 0.0
x_19_11_H: 0.0
x_19_11_P: 0.0
x_19_11_Z: 0.0
x_19_120_H: 1.

x_21_47_H: 0.0
x_21_47_P: 0.0
x_21_47_Z: 1.0
x_21_48_H: 0.0
x_21_48_P: 0.0
x_21_48_Z: 0.0
x_21_49_H: 0.0
x_21_49_P: 0.0
x_21_49_Z: 0.0
x_21_4_H: 0.0
x_21_4_P: 0.0
x_21_4_Z: 0.0
x_21_50_H: 0.0
x_21_50_P: 0.0
x_21_50_Z: 0.0
x_21_51_H: 0.0
x_21_51_P: 0.0
x_21_51_Z: 0.0
x_21_52_H: 0.0
x_21_52_P: 0.0
x_21_52_Z: 0.0
x_21_53_H: 0.0
x_21_53_P: 0.0
x_21_53_Z: 0.0
x_21_54_H: 0.0
x_21_54_P: 0.0
x_21_54_Z: 0.0
x_21_55_H: 0.0
x_21_55_P: 0.0
x_21_55_Z: 0.0
x_21_56_H: 0.0
x_21_56_P: 0.0
x_21_56_Z: 0.0
x_21_57_H: 0.0
x_21_57_P: 0.0
x_21_57_Z: 0.0
x_21_58_H: 0.0
x_21_58_P: 0.0
x_21_58_Z: 0.0
x_21_59_H: 0.0
x_21_59_P: 0.0
x_21_59_Z: 0.0
x_21_5_H: 0.0
x_21_5_P: 0.0
x_21_5_Z: 0.0
x_21_60_H: 0.0
x_21_60_P: 0.0
x_21_60_Z: 0.0
x_21_61_H: 0.0
x_21_61_P: 0.0
x_21_61_Z: 0.0
x_21_62_H: 0.0
x_21_62_P: 0.0
x_21_62_Z: 0.0
x_21_63_H: 0.0
x_21_63_P: 0.0
x_21_63_Z: 0.0
x_21_64_H: 0.0
x_21_64_P: 0.0
x_21_64_Z: 0.0
x_21_65_H: 0.0
x_21_65_P: 0.0
x_21_65_Z: 0.0
x_21_66_H: 0.0
x_21_66_P: 0.0
x_21_66_Z: 0.0
x_21_67_H: 0.0
x

...

C1_constraint_for_student_14_at_time_slot_88_location_H: 0.0
C1_constraint_for_student_14_at_time_slot_88_location_P: 0.0
C1_constraint_for_student_14_at_time_slot_89_location_Z: 0.0
C1_constraint_for_student_14_at_time_slot_89_location_H: 0.0
C1_constraint_for_student_14_at_time_slot_89_location_P: 0.0
C1_constraint_for_student_14_at_time_slot_90_location_Z: 0.0
C1_constraint_for_student_14_at_time_slot_90_location_H: 0.0
C1_constraint_for_student_14_at_time_slot_90_location_P: 0.0
C1_constraint_for_student_14_at_time_slot_91_location_Z: 0.0
C1_constraint_for_student_14_at_time_slot_91_location_H: 0.0
C1_constraint_for_student_14_at_time_slot_91_location_P: 0.0
C1_constraint_for_student_14_at_time_slot_92_location_Z: 0.0
C1_constraint_for_student_14_at_time_slot_92_location_H: 0.0
C1_constraint_for_student_14_at_time_slot_92_location_P: 0.0
C1_constraint_for_student_14_at_time_slot_93_location_Z: 0.0
C1_constraint_for_student_14_at_time_slot_93_location_H: 0.0
C1_constraint_for_studen

C1_constraint_for_student_20_at_time_slot_42_location_Z: 0.0
C1_constraint_for_student_20_at_time_slot_42_location_H: 0.0
C1_constraint_for_student_20_at_time_slot_42_location_P: 0.0
C1_constraint_for_student_20_at_time_slot_43_location_Z: 0.0
C1_constraint_for_student_20_at_time_slot_43_location_H: 0.0
C1_constraint_for_student_20_at_time_slot_43_location_P: 0.0
C1_constraint_for_student_20_at_time_slot_44_location_Z: 0.0
C1_constraint_for_student_20_at_time_slot_44_location_H: 0.0
C1_constraint_for_student_20_at_time_slot_44_location_P: 0.0
C1_constraint_for_student_20_at_time_slot_45_location_Z: 0.0
C1_constraint_for_student_20_at_time_slot_45_location_H: 0.0
C1_constraint_for_student_20_at_time_slot_45_location_P: 0.0
C1_constraint_for_student_20_at_time_slot_46_location_Z: 0.0
C1_constraint_for_student_20_at_time_slot_46_location_H: 0.0
C1_constraint_for_student_20_at_time_slot_46_location_P: 0.0
C1_constraint_for_student_20_at_time_slot_47_location_Z: 0.0
C1_constraint_for_studen

C1_constraint_for_student_25_at_time_slot_56_location_H: 0.0
C1_constraint_for_student_25_at_time_slot_56_location_P: 0.0
C1_constraint_for_student_25_at_time_slot_57_location_Z: 0.0
C1_constraint_for_student_25_at_time_slot_57_location_H: 0.0
C1_constraint_for_student_25_at_time_slot_57_location_P: 0.0
C1_constraint_for_student_25_at_time_slot_58_location_Z: 0.0
C1_constraint_for_student_25_at_time_slot_58_location_H: 0.0
C1_constraint_for_student_25_at_time_slot_58_location_P: 0.0
C1_constraint_for_student_25_at_time_slot_59_location_Z: 0.0
C1_constraint_for_student_25_at_time_slot_59_location_H: 0.0
C1_constraint_for_student_25_at_time_slot_59_location_P: 0.0
C1_constraint_for_student_25_at_time_slot_60_location_Z: 0.0
C1_constraint_for_student_25_at_time_slot_60_location_H: 0.0
C1_constraint_for_student_25_at_time_slot_60_location_P: 0.0
C1_constraint_for_student_25_at_time_slot_61_location_Z: 0.0
C1_constraint_for_student_25_at_time_slot_61_location_H: 0.0
C1_constraint_for_studen

C1_constraint_for_student_30_at_time_slot_14_location_H: 0.0
C1_constraint_for_student_30_at_time_slot_14_location_P: 0.0
C1_constraint_for_student_30_at_time_slot_23_location_Z: 0.0
C1_constraint_for_student_30_at_time_slot_23_location_H: 0.0
C1_constraint_for_student_30_at_time_slot_23_location_P: 0.0
C1_constraint_for_student_30_at_time_slot_24_location_Z: 0.0
C1_constraint_for_student_30_at_time_slot_24_location_H: 0.0
C1_constraint_for_student_30_at_time_slot_24_location_P: 0.0
C1_constraint_for_student_30_at_time_slot_25_location_Z: 0.0
C1_constraint_for_student_30_at_time_slot_25_location_H: 0.0
C1_constraint_for_student_30_at_time_slot_25_location_P: 0.0
C1_constraint_for_student_30_at_time_slot_26_location_Z: 0.0
C1_constraint_for_student_30_at_time_slot_26_location_H: 0.0
C1_constraint_for_student_30_at_time_slot_26_location_P: 0.0
C1_constraint_for_student_30_at_time_slot_27_location_Z: 0.0
C1_constraint_for_student_30_at_time_slot_27_location_H: 0.0
C1_constraint_for_studen

C4_upperbound_constraint_for_time_slot_71_at_Pop_Health: -147.0
C4_lowerbound_constraint_for_time_slot_71_at_Pop_Health: -144.0
C4_upperbound_constraint_for_time_slot_72_at_Pop_Health: -3.0
C4_lowerbound_constraint_for_time_slot_72_at_Pop_Health: 0.0
C4_upperbound_constraint_for_time_slot_73_at_Pop_Health: -3.0
C4_lowerbound_constraint_for_time_slot_73_at_Pop_Health: 0.0
C4_upperbound_constraint_for_time_slot_74_at_Pop_Health: -146.0
C4_lowerbound_constraint_for_time_slot_74_at_Pop_Health: -143.0
C4_upperbound_constraint_for_time_slot_75_at_Pop_Health: -3.0
C4_lowerbound_constraint_for_time_slot_75_at_Pop_Health: 0.0
C4_upperbound_constraint_for_time_slot_76_at_Pop_Health: -3.0
C4_lowerbound_constraint_for_time_slot_76_at_Pop_Health: 0.0
C4_upperbound_constraint_for_time_slot_77_at_Pop_Health: -3.0
C4_lowerbound_constraint_for_time_slot_77_at_Pop_Health: 0.0
C4_upperbound_constraint_for_time_slot_78_at_Pop_Health: 0.0
C4_lowerbound_constraint_for_time_slot_78_at_Pop_Health: 3.0
C4_uppe

In [355]:
output = []
for var in model.variables():
    if var.value() == 1:
        output.append(var.name)

In [356]:
df = pd.DataFrame(columns = ['Student', 'Shift Time', 'Location'])
for line in output:
    df = df.append({'Student' : line.split('_')[1], 'Shift Time' : line.split('_')[2], 'Location' : line.split('_')[3]}, 
                ignore_index = True)

In [341]:
df.to_excel(r"./output.xlsx")

In [357]:
df

Student Shift Time Location
0        10        134        Z
1        10         20        H
2        10         76        H
3        11         37        Z
4        12        104        H
..      ...        ...      ...
175       6         96        Z
176      70         37        H
177      70         76        H
178       7        102        Z
179       7         50        Z

[180 rows x 3 columns]

In [199]:
for var in model.variables():
    if var.value() == 1:
        print(var.name)